In [1]:
import pandas as pd
import numpy as np

from collections import Counter
import matplotlib.pyplot as plt
%matplotlib inline

from scipy import sparse
from sklearn.decomposition import NMF

In [2]:
#!unzip repeat_consumption_data.zip -d data

In [3]:
train = pd.read_csv('data/data/reddit_sample/train.csv')
test = pd.read_csv('data/data/reddit_sample/test.csv')
validation = pd.read_csv('data/data/reddit_sample/validation.csv')

In [4]:
train.columns = ['id1', 'id2', 'id3']
test.columns  = ['id1', 'id2', 'id3']
validation.columns = ['id1', 'id2', 'id3']

In [5]:
train.shape , test.shape, validation.shape

((379549, 3), (104308, 3), (112246, 3))

In [6]:
train['id1'].max(), train['id2'].max() 

(20023, 21385)

In [7]:
n_rows = train['id1'].max()
n_cols = train['id2'].max()

In [8]:
def get_dense_matrix(row,col,data):
    return (sparse.coo_matrix((data, (row, col)), shape=(n_rows+1, n_cols+1)).toarray())

In [9]:
train_mat = get_dense_matrix(train['id1'], train['id2'], train['id3'])
test_mat = get_dense_matrix(test['id1'], test['id2'], test['id3'])
val_mat = get_dense_matrix(validation['id1'], validation['id2'], validation['id3'])

In [10]:
import gc
gc.collect()

111

Data is very sparse. Let's try to predict the missing values. We do it by matrix factorization. The concept is that we divide the orginal sparse matrix into 2 different matrices one which defines user attributes and another which defines item attributes. Now by multiplying back these 2 matrices we can fill the missing values. 

In [11]:
train_csc =  sparse.csr_matrix((train['id3'], (train['id1'], train['id2'])),  shape=(n_rows+1, n_cols+1))


In [40]:
def RMSE(original, predicted):
    xs, ys = original.nonzero()
    error = 0
    count = 0
    for x, y in zip(xs, ys):
        error += pow(original[x, y] - predicted[x, y], 2)
        count += 1 
    return np.sqrt(error/count)

In [36]:
print(zip(xs ,ys))

In [13]:
model = NMF(n_components=500, init='random', random_state=0)
W = model.fit_transform(train_csc)
print( model.reconstruction_err_)

8684.844263621208


In [14]:
H = model.components_

In [15]:
predicted = np.dot(W, H)

In [16]:
train_rmse = RMSE(train_mat, predicted)
test_rmse = RMSE(test_mat, predicted)
val_rmse = RMSE(val_mat, predicted)

In [17]:
print("train rmse = ", train_rmse)
print("test rmse = ", test_rmse)
print("val rmse = ", val_rmse)

train rmse =  8247.434196849505
test rmse =  42795.36569361117
val rmse =  41816.338165389185


model  is clearly over-fitting. 

In [21]:
predicted = np.zeros(shape = (n_rows+1, n_cols+1), dtype = "float")

In [43]:
error = float("inf")
e_train_arr = []
e_val_arr = []
for k in range(10, 100 , 20):
    model = NMF(n_components=k, init='random', random_state=0)
    W = model.fit_transform(train_csc)
    H = model.components_
    print("k = ", k , "error = ", model.reconstruction_err_)
    if  model.reconstruction_err_ < error:
        predicted = np.dot(W,H)
        error = model.reconstruction_err_ 
        e_train = RMSE(train_mat, predicted)
        e_val   = RMSE(val_mat, predicted)
        e_train_arr.append(e_train)
        e_val_arr.append(e_val)
        print("train rmse = ", e_train)
        print("val rmse = ", e_val)
"""
this gives o/p as follows
k =  50 error =  27555.41514203906
k =  70 error =  24922.231314578425
k =  90 error =  22994.866819216677
k =  110 error =  21460.782796146825
k =  130 error =  20014.723246779147

clearly as K increases acc is increasing but the cost of computation increases.
We have 21K items choosing 10% of the original feature dimension . 
"""
 

k =  10 error =  39672.09446184758
train rmse =  64.10446954625985
val rmse =  87.18462968880965
k =  30 error =  31521.070748706778
train rmse =  50.46419888716609
val rmse =  103.69574765962068
k =  50 error =  27555.41514203906
train rmse =  44.03826144024137
val rmse =  109.49234337653924
k =  70 error =  24922.231314578425
train rmse =  39.76135550329401
val rmse =  112.65331923468831
k =  90 error =  22994.866819216677
train rmse =  36.25243025389681
val rmse =  114.63341223156992


'\nthis gives o/p as follows\nk =  50 error =  27555.41514203906\nk =  70 error =  24922.231314578425\nk =  90 error =  22994.866819216677\nk =  110 error =  21460.782796146825\nk =  130 error =  20014.723246779147\n\nclearly as K increases acc is increasing but the cost of computation increases.\nWe have 21K items choosing 10% of the original feature dimension . \n'

Observation : As we increase the number of latent factors , training error is decreasing but validation error is increasing indiating over-fitting. 

In [44]:
test_rmse = RMSE(test_mat, predicted)

In [45]:
test_rmse

122.66684699121222

In [70]:
"""
@INPUT:
    R     : a matrix to be factorized, dimension N x M
    V     : validation matrix
    P     : an initial matrix of dimension N x K
    Q     : an initial matrix of dimension M x K
    K     : the number of latent features
    steps : the maximum number of steps to perform the optimisation
    alpha : the learning rate
    beta  : the regularization parameter
@OUTPUT:
    the final matrices P and Q
"""
def RMSE_sgd(R , P, Q, K, beta=0.02):
    e = 0
    for i in range(len(R)):
        for j in range(len(R[i])):
            if R[i][j] > 0: 
                #print(R[i][j] , np.dot(P[i,:],Q[:,j]))
                power = pow(R[i][j] - np.dot(P[i,:],Q[:,j]), 2)
                print(e, power)
                e = e + power
                for k in range(K):
                    e = e + (beta/2) * ( pow(P[i][k],2) + pow(Q[k][j],2) )
    return e;

def matrix_factorization(R, V, P, Q, K, steps=5000, alpha=0.0002, beta=0.02):
    Q = Q.T
    
    # Initializing the bias terms
    b_u = np.zeros(len(R))
    b_i = np.zeros(len(R[0]))
    b = np.mean(R[np.where(R != 0)])
    
    for step in range(0, steps):
        for i in range(0, len(R)):
            for j in range(len(R[i])):
                if R[i][j] > 0:
                    eij = R[i][j] - np.dot(P[i,:],Q[:,j])
                   # print(eij)
                    for k in range(K):
                        P[i][k] = P[i][k] + alpha * (2 * eij * Q[k][j] - beta * P[i][k])
                        Q[k][j] = Q[k][j] + alpha * (2 * eij * P[i][k] - beta * Q[k][j])
            #print(np.dot(P[i,:],Q[:,j]))
        #eR = np.dot(P,Q)
        e_train = RMSE_sgd(R,P,Q,k,beta)
        e_val   = RMSE_sgd(V,P,Q,k,beta)   
        #if e_train < 0.001:
        #    break
        
        if (step % 20 == 0):
            print("--------------------------------------------------------")
            print("step = ", step ," e_train = ", e_train , " e_val = " , e_val)
            print("--------------------------------------------------------")
    return P, Q.T

In [63]:
# this method is giving nan during reconstruction. This might be because the original matrix is very poorly conditioned.
K = 50

P = np.random.normal(scale=1./K, size=(n_rows + 1, K))
Q = np.random.normal(scale=1./K, size=(n_cols + 1, K))

nP, nQ = matrix_factorization(train_mat, val_mat, P, Q, K)

/home/nilesh/anaconda3/envs/compete/lib/python3.7/site-packages/ipykernel_launcher.py:42: RuntimeWarning: overflow encountered in double_scalars
/home/nilesh/anaconda3/envs/compete/lib/python3.7/site-packages/ipykernel_launcher.py:43: RuntimeWarning: overflow encountered in double_scalars
/home/nilesh/anaconda3/envs/compete/lib/python3.7/site-packages/ipykernel_launcher.py:42: RuntimeWarning: invalid value encountered in double_scalars
/home/nilesh/anaconda3/envs/compete/lib/python3.7/site-packages/ipykernel_launcher.py:43: RuntimeWarning: invalid value encountered in double_scalars


0 nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan 143.96848671505427
nan 15.983134886758943
nan 440.9614963771983
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan 35.980150440405794
nan 1935.6085121508206
nan 4.005536236153658
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan 1.0051064116248984
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan

/home/nilesh/anaconda3/envs/compete/lib/python3.7/site-packages/ipykernel_launcher.py:20: RuntimeWarning: overflow encountered in double_scalars
/home/nilesh/anaconda3/envs/compete/lib/python3.7/site-packages/ipykernel_launcher.py:24: RuntimeWarning: overflow encountered in double_scalars


 nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan nan
nan

NameError: name 'e_val' is not defined

In [ ]:
# open items
# try fast AI NMF functions
# try deep learning models for recommender system
# try paper implementations for recommendation in sparse matrices. 